# RaveGenerator2 Sample Dumper 💀

This Notebook extracts embedded audio samples from the Linux version of the VST Plugin RaveGenerator2.
So you can do dirty rave sounds directly in your sampler of choice and without installing Qt4 (see https://discourse.ardour.org/t/rave-generator-2-vst-no-gui-amd-graphics/107099/3).

Get the plugin here: https://blog.wavosaur.com/rave-generator-2-vst-audiounit-the-stab-machine-is-back-in-the-house/ (RaveGenerator2-Linux.tar.gz)

Contained should be a file `RaveGenerator2VST-x64.so` that looks like:

```console
$ file RaveGenerator2VST-x64.so
RaveGenerator2VST-x64.so: ELF 64-bit LSB shared object, x86-64, version 1 (SYSV), dynamically linked, BuildID[sha1]=aeb7c5c39b06d96e0f5dc629457a66bc07522965, stripped

$ sha512sum RaveGenerator2VST-x64.so 
c32d1d7834075ddaab09305ef00020375f41ba4a420789e125778e26260da578c4f65d9e02d3ec08a6ee861643edda344e385c2d99351626ab61ba2b9c1909f0  RaveGenerator2VST-x64.so
```

Tested with:
* Ghidra v10.1.15
* https://github.com/GhidraJupyter/ghidra-jupyter-kotlin v1.5.1

## Usage

1. Run Ghidra, throw `RaveGenerator2VST-x64.so` in there, and analyze it
2. Start GhidraJupyterKotlin kernel and open this notebook
3. Run the following two blocks
4. You will get all the contained samples as `.wav` files like:
```
ravegen_stabs3_Gabbers_C3.wav
ravegen_stabs3_Hardcore Hoover_D#2.wav
ravegen_stabs3_Hound Stab_C3.wav
ravegen_stabs3_House Nation_C3.wav
ravegen_stabs3_Magic Feet_C3.wav
ravegen_stabs3_Mayday_C3.wav
...
```

## Run

1. Select Output dir

In [16]:
var outDir = askDirectory("Select Audio Save Directory", "Select")

2. Find embedded samples and extract them to outDir

In [294]:
import GhidraJupyterKotlin.extensions.address.*

import ghidra.program.model.listing.Function
import ghidra.program.model.address.GenericAddress
import ghidra.program.model.address.AddressSet
import ghidra.program.model.data.WAVEDataType
import ghidra.program.model.data.Playable
import ghidra.app.util.exporter.BinaryExporter
import org.apache.commons.io.FilenameUtils
import java.io.File

data class RGSample(var fileName: String? = null,
                    var resourceName: String? = null,
                    var waveAddr: GenericAddress? = null,
                    var rootNote: String? = null) {
    fun valid(): Boolean {
        return fileName != null && resourceName != null && waveAddr != null
    }
}

fun getRootNoteString(arg: Long): String {
    // Sample::setRootNote(int) pitches the note up or down by the given number of semitones away from 60 (= C3)
    // written as python:
    // factor = 1.0
    // if note > 60:
    //     for i in range(note - 60):
    //         factor /= 1.059463094359  # <- google that factor, it's the frequency ratio between to adjacent semitones
    // elif note < 60:
    //     for i in range(60 - note):
    //         factor *= 1.059463094359

    // convert that number to a readable note, assuming C3=60, B2=59, C#3=61,...
    val octave = (arg / 12).toInt() - 2
    val semitone = (arg % 12).toInt()
    val notes = arrayOf("C", "C#", "D", "D#", "E", "F", "F#", "G", "G#", "A", "A#", "B")
    
    return "${notes[semitone]}${octave}"
}

fun run() {
    val debugPathToBuffer = false
    val debugAdjustRootNote = false
    val infoAdjustRootNote = true
    val fileNamePrefix = "ravegen_"
    
    if (outDir == null || !outDir.isDirectory()) {
        println("select output dir first")
        return
    }

    // search functions
    var pathToBuffer: Function? = null
    var adjustRootNote: Function? = null
    
    val fm = currentProgram.getFunctionManager()
    for (f in fm.getFunctions(true)) {
        when (f.name) {
            "pathToBuffer" -> {
                val functionLen = f.body.numAddresses
                if (functionLen <= 6) {
                    // ignore thunk
                    continue
                }
                println("found ${f} at ${f.entryPoint} len ${functionLen}")
                pathToBuffer = f
            }
            "adjustRootNote" -> {
                val functionLen = f.body.numAddresses
                if (functionLen <= 6) {
                    // ignore thunk
                    continue
                }
                println("found ${f} at ${f.entryPoint} len ${functionLen}")
                adjustRootNote = f
            }
        }
    }
    
    if (pathToBuffer == null) {
        println("pathToBuffer not found")
        return
    }
    
    if (adjustRootNote == null) {
        println("adjustRootNote not found")
        return
    }
    
    println("---")
    
    // get root notes
    val defaultRootNote = getRootNoteString(60)
    val rootNotes = hashMapOf<String, String>()
    var currentResource = ""
    
    // parse adjustRootNote.
    // that function contains some mappings from sample resource names to different root notes
    // (default is probably C3 or something).
    // we want to translate those to readable notes like C/D/E.. to add to the output file name.
    for (codeUnit in currentProgram.listing.getCodeUnits(adjustRootNote.body, true)) {
        if (monitor.isCancelled) {
            return
        }
        
        val mnem = codeUnit.mnemonicString
        if (mnem == "LEA") {
            // resource name loading is the same as in pathToBuffer
            if (debugAdjustRootNote) {
                println("${codeUnit.address}: $codeUnit")
            }
            
            if (currentResource != "") {
                println("ERROR: we missed root note data")
            }
            
            // load resource name
            val resourceNameAddr = codeUnit.getAddress(1)
            val resourceName = getDataAt(resourceNameAddr).getValue() as String
            currentResource = resourceName
        } else if (mnem == "JZ") {
            if (debugAdjustRootNote) {
                println("${codeUnit.address}: $codeUnit")
            }
                
            // follow the jump target for the case of the resource name matching
            val jmpTarget = codeUnit.getAddress(0)
            for (nestedCU in currentProgram.listing.getCodeUnits(jmpTarget, true)) {
                if (debugAdjustRootNote) {
                    println("NEST ${nestedCU.address}: $nestedCU")
                }

                if (nestedCU.mnemonicString.startsWith("J")) {
                    // stop at the jump back to avoid cycles
                    break
                } else if (nestedCU.toString().startsWith("MOV ESI,")) {
                    if (currentResource == "") {
                        println("ERROR: we missed the root note name")
                    }

                    // ex: MOV ESI,0x38
                    // get argument to call of Sample::setRootNote()
                    val rootNoteRaw = nestedCU.getScalar(1).getValue()
                    val rootNote = getRootNoteString(rootNoteRaw)

                    // write root note
                    if (debugAdjustRootNote || infoAdjustRootNote) {
                        println("got root note: ${currentResource} -> ${rootNote}")
                    }

                    rootNotes[currentResource] = rootNote
                    currentResource = ""
                }
            }
        } else if (mnem == "POP" && codeUnit.toString() == "POP RBP") {
            if (debugAdjustRootNote) {
                println("end of function")
            }
            break
        }
    }
    
    // get sample references
    val samples = mutableListOf<RGSample>()
    var currentSample = RGSample()
    
    // parse asm listing of pathToBuffer.
    // pathToBuffer contains something like a QResource lookup table where resource names like
    // ":/Resources/foo/bar.wav" are mapped to memory references to content of the bundled file.
    for (codeUnit in currentProgram.listing.getCodeUnits(pathToBuffer.body, true)) {
        if (monitor.isCancelled) {
            return
        }
        
        val mnem = codeUnit.mnemonicString
        if (mnem == "LEA") {
            // load resource name
            val resourceNameAddr = codeUnit.getAddress(1)
            val resourceName = getDataAt(resourceNameAddr).getValue() as String
            currentSample.resourceName = resourceName
            currentSample.fileName = resourceName.removePrefix(":/Resources/")
            
            if (debugPathToBuffer) {
                println("${codeUnit.address}: ${resourceNameAddr} ${resourceName}")
            }
        } else if (mnem.contains("MOV") && codeUnit.toString().contains(" RAX,")) {
            // set function return value, probably
            val wavePtr = if (mnem.startsWith("CMOV")) {
                getDataAt(codeUnit.getAddress(1)).getValue()
            } else {
                codeUnit.getAddress(0)
            } as GenericAddress
            
            currentSample.waveAddr = wavePtr
            currentSample.rootNote = if (currentSample.resourceName in rootNotes) {
                rootNotes[currentSample.resourceName]
            } else {
                defaultRootNote
            }
            // this sample is done
            samples.add(currentSample)
            
            if (debugPathToBuffer) {
                println("${codeUnit.address}: wave address ${wavePtr}")
            }
            
            // next sample
            currentSample = RGSample()
        }
    }
    
    println("---")
    // export sound files with nice names
    val binaryExporter = BinaryExporter()
    for (sample in samples) {
        if (monitor.isCancelled) {
            return
        }
        
        // sanity checks
        if (!sample.valid()) {
            println("invalid RGSample")
            continue
        }
        
        val wave = getDataAt(sample.waveAddr)
        if (wave.getValue() !is Playable) {
            println("got unplayable wave")
            continue
        }
        
        // get wave byte range
        val startAddr = sample.waveAddr!!
        val addressSet = AddressSet(startAddr, startAddr + wave.getLength())
        
        // build output file name
        // NOTE i'm not sure if the path splitting works on Windows because of the forward slashes
        val origDirName = FilenameUtils.getName(FilenameUtils.getPathNoEndSeparator(sample.fileName))
        val origFileName = FilenameUtils.removeExtension(FilenameUtils.getName(sample.fileName))
        var fileExtension = FilenameUtils.getExtension(sample.fileName)
        val fileName = "${fileNamePrefix}${origDirName}_${origFileName}_${sample.rootNote}.${fileExtension}"
        // this is something like "ravegen_stabs2_Awesome3_G#3.wav"
        val outputTarget = FilenameUtils.concat(outDir.absolutePath, fileName)
        
        println("exporting sample at addr=${startAddr} len=${wave.getLength()} root=${sample.rootNote} -> ${fileName}")

        // write to output file
        val outputFile = File(outputTarget)
        if (outputFile.exists()) {
            println("output file already exists, skipping")
            continue
        }
        
        binaryExporter.export(outputFile, currentProgram, addressSet, monitor)
    }
    println("done")
}

run()

found Sample::adjustRootNote at 001201a0 len 904
found Sample::pathToBuffer at 00120b20 len 2331
---
got root note: :/Resources/sounds/instrus/Get Up.wav -> G#2
got root note: :/Resources/sounds/stabs3/Hardcore Hoover.wav -> D#2
got root note: :/Resources/sounds/stabs2/HappyHardcoreStab.wav -> D#3
got root note: :/Resources/sounds/stabs2/BizarreInc1.wav -> E3
got root note: :/Resources/sounds/stabs2/FidelFattiPiano.wav -> D3
got root note: :/Resources/sounds/stabs2/Awesome3.wav -> G#3
got root note: :/Resources/sounds/instrus/Pizzicato Dance.wav -> F#3
got root note: :/Resources/sounds/stabs2/Dist Brazil.wav -> A#2
got root note: :/Resources/sounds/instrus/Mayday Dream.wav -> D3
got root note: :/Resources/sounds/instrus/Rave CutBass.wav -> D4
got root note: :/Resources/sounds/instrus/Juno Bass.wav -> F4
got root note: :/Resources/sounds/stabs2/Short Rave.wav -> D#3
got root note: :/Resources/sounds/instrus/Pump Bass.wav -> D3
got root note: :/Resources/sounds/stabs3/Break Boys.wav -> F

exporting sample at addr=0072df40 len=45268 root=C3 -> ravegen_voices_Loon_C3.wav
exporting sample at addr=00739014 len=171046 root=C3 -> ravegen_voices_Neneh Cherry_C3.wav
exporting sample at addr=00762c3a len=196436 root=C3 -> ravegen_voices_ooooooooh_C3.wav
exporting sample at addr=00792b8e len=123990 root=C3 -> ravegen_voices_ooooooooh2_C3.wav
exporting sample at addr=007b0fe4 len=318180 root=C3 -> ravegen_voices_Party_C3.wav
exporting sample at addr=007feac8 len=30164 root=C3 -> ravegen_voices_Paw_C3.wav
exporting sample at addr=0080609c len=280496 root=C#3 -> ravegen_voices_Patti_C#3.wav
done
